In [1]:
import altair as alt
import numpy as np
import pandas as pd

Parameters:

In [2]:
muX, muY = 4, 4
sigmaX, sigmaY = 3, 3
sigmaD = 0.5  # equivalent to 1/2
dAverage = np.sqrt(muX**2 + muY**2)

2D Gaussian function $f(x, y)$:

In [3]:
def f_xy(x, y):
    return (
        1
        / (2 * np.pi * sigmaX * sigmaY)
        * np.exp(
            -(((x - muX) ** 2) / (2 * sigmaX**2) + ((y - muY) ** 2) / (2 * sigmaY**2))
        )
    )

Distance Gaussian $f_D(d, x, y)$:

In [4]:
def fD(d, x, y):
    return (
        1
        / (np.sqrt(2 * np.pi) * sigmaD)
        * np.exp(-((d - np.sqrt(x**2 + y**2)) ** 2) / (2 * sigmaD**2))
    )

Combined function $f(x, y, d)$:

In [5]:
def f_xy_d(x, y, d):
    return fD(d, x, y) * f_xy(x, y)

Interactive plotting function: one panel for $f(x, y)$, the other for $f(x, y, d)$ with a circle of radius $d$.

In [6]:
def update_plot():
    alt.data_transformers.disable_max_rows()
    # Create a grid for x and y over the domain [-10, 10]
    x = np.linspace(-10, 10, 200)
    y = np.linspace(-10, 10, 200)
    X, Y = np.meshgrid(x, y)
    step = x[1] - x[0]

    # Prepare a base dataframe with unconditional f(x,y)
    df_base = pd.DataFrame(
        {
            "x": X.ravel(),
            "y": Y.ravel(),
            "x2": (X + step).ravel(),
            "y2": (Y + step).ravel(),
            "value_uncond": f_xy(X, Y).ravel(),
        }
    )

    # Left chart: Unconditional f(x,y)
    left_chart = (
        alt.Chart(df_base)
        .mark_rect()
        .encode(
            x=alt.X("x:Q", title="x"),
            x2=alt.X2("x2:Q"),
            y=alt.Y("y:Q", title="y"),
            y2=alt.Y2("y2:Q"),
            color=alt.Color("value_uncond:Q", scale=alt.Scale(scheme="viridis")),
        )
        .properties(width=300, height=300, title="Unconditional f(x,y)")
    )

    # Define a slider parameter for d using pure Altair
    d_slider = alt.param(
        "d",
        bind=alt.binding_range(
            min=float(dAverage) - 2, max=float(dAverage) + 2, step=0.1, name="d"
        ),
        value=float(dAverage),
    )

    # Right chart: Compute conditional f(x,y,d) with transform_calculate.
    # The expression below mirrors:
    #   f_xy_d = fD(d, x, y) * f_xy(x, y)
    #   where fD(d,x,y) = 1/(sqrt(2*PI)*sigmaD) * exp(-((d - sqrt(x**2+y**2))**2)/(2*sigmaD**2))
    right_chart = (
        alt.Chart(df_base)
        .transform_calculate(
            value=(
                "datum.value_uncond / (sqrt(2*PI) * {sd}) * "
                "exp(- (pow(d - sqrt(pow(datum.x,2) + pow(datum.y,2)), 2)) / (2*{sd}*{sd}))"
            ).format(sd=sigmaD)
        )
        .mark_rect()
        .encode(
            x=alt.X("x:Q", title="x"),
            x2=alt.X2("x2:Q"),
            y=alt.Y("y:Q", title="y"),
            y2=alt.Y2("y2:Q"),
            color=alt.Color("value:Q", scale=alt.Scale(scheme="viridis")),
        )
        .properties(width=300, height=300, title="Conditional f(x, y, d)")
        .add_params(d_slider)
    )

    # Create a unit circle data frame for overlay
    theta = np.linspace(0, 2 * np.pi, 100)
    circle_df = pd.DataFrame({"x": np.cos(theta), "y": np.sin(theta)})

    # In the circle chart, scale the unit circle by the slider value d
    circle = (
        alt.Chart(circle_df)
        .transform_calculate(
            x_scaled="datum.x * d",
            y_scaled="datum.y * d",
        )
        .mark_line(color="gray", strokeWidth=1)
        .encode(
            x=alt.X("x_scaled:Q"),
            y=alt.Y("y_scaled:Q"),
        )
        .add_params(d_slider)
    )

    # Combine the circle with the right chart
    right_chart = right_chart + circle

    # Display the charts side by side
    combined_chart = alt.hconcat(left_chart, right_chart)
    combined_chart.display()

Create the interactive slider for $d$

In [7]:
update_plot()

alt.HConcatChart(...)